# Coffee Market Analysis
## Data-Wrangling Notebook

### Matthew Garton - February 2019

**Purpose:** The purpose of this notebook is to acquire my data, inspect it, clean it and prepare it for EDA and modeling.

**Context**: The ultimate goal of my project is to develop trading signals for coffee futures. I will attempt to build a machine learning model which uses fundamental and technical data to predict the future direction of coffee futures price changes. My expectation at the outset of this project is that my feature matrix will include data on weather, GDP, and coffee production and exports in major coffee-producing nations, GDP and coffee import data in major coffee-importing nations, as well as volume, open-interest, and commitment of traders data for ICE coffee futures contracts.

Note that many of the decisions made and functions written here came up at various stages of the project, from initial inspection all the way to model-building (as is the non-linear nature of the data science workflow). To keep things clean, I have moved all of the data cleaning/prep (outside of train-test splitting and some feature engineering) to this notebook. The csv file that I output can then be accessed in other notebooks in this repository.

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import datetime

pd.options.display.max_columns = 1000
pd.options.display.max_rows = 1000
%matplotlib inline

import warnings
warnings.filterwarnings("ignore")

## Gathering data

1. Price data (1973-2019) - daily OHLC prices (plus Volume and OI) for ICE Coffee 'C' futures.

    source: [Wiki Continuous Futures database on Quandl](https://www.quandl.com/data/CHRIS-Wiki-Continuous-Futures)
      
      
2. Weather data (1991-2015) - monthly average temperature (celsius) and rainfall (mm) for the top five coffee exporting countries (Brazil, Vietnam, Colombia, Indonesia, Ethiopia).
    
    source: [World Bank Climate Change Knowledge Portal](http://sdwebx.worldbank.org/climateportal/index.cfm?page=downscaled_data_download&menu=historical)
    
    
3. Fundamental data (1990-2017) - annual data on coffee production, imports, exports, etc. from International Coffee Organization*.

    source: [International Coffee Organization](http://www.ico.org/new_historical.asp?section=Statistics)


4. Positioning data (1995-2016) - monthly Commitment of Traders' reports from CFTC

    source: [Commodity Futures Trading Commission](https://www.cftc.gov/MarketReports/CommitmentsofTraders/HistoricalCompressed/index.htm)
    
*Note: Before getting started here, I did some initial data assembling/cleaning in excel, so if you choose to get the data directly from the sources listed above, some preparation will be necessary before getting it into the format shown here. The biggest decision I made so far was in how to handle some of the ICO data which was indexed by 'Crop Year' rather than 'Calendar Year'. My initial solution is to treat the most recent year of the 'Crop Year' as the relevant 'year' for the data (so Crop Year 1991/1992 is treated as Year 1992, with the understanding that all of the data for the 1991-1992 period would have been availably by EOY 1992). For now, this is a simplifying assumption to avoid any 'look-ahead bias.' This might be an oversimplification that I'll have to come back to. 

In [2]:
# import Daily ICE Coffee 'C' Futures price data
coffee = pd.read_csv('../data/CHRIS-ICE_KC1.csv')

# import Monthly Weather data for major coffee producing countries
weather = pd.read_csv('../data/Weather.csv')

# import Annual fundamental (Production, Exports, Imports, etc.) data
fundamental = pd.read_csv('../data/SupplyDemand.csv')

# import Monthly Commitment of Traders report data
cot = pd.read_csv('../data/CommitmentOfTraders.csv')

In [3]:
# Quick fix to 'Country' column typo..
weather.rename(index=str, columns={' Country':'Country'}, inplace=True)
weather.head()

Date Country  Temperature (Monthly – C)  Precip (mm)
0  01/31/91     BRA                    25.6430      260.878
1  02/28/91     BRA                    25.9575      193.859
2  03/31/91     BRA                    25.6557      238.866
3  04/30/91     BRA                    25.3129      194.848
4  05/31/91     BRA                    24.7910      119.090

In [4]:
# For each dataframe, index by Date (as datetime object) and extract year, month
dfs = [coffee, weather, fundamental, cot]
for df in dfs:
    df['Date'] = pd.to_datetime(df['Date'])
    df.set_index('Date', inplace=True)
    
# coffee and cot are sorted backwards; reverse order
coffee.sort_index(inplace=True)
cot.sort_index(inplace=True);

Market_and_Exchange_Names  \
Date                                                      
1995-03-21                     COFFEE C - CSCE COFFEE C   
1995-03-28                     COFFEE C - CSCE COFFEE C   
1995-04-04                     COFFEE C - CSCE COFFEE C   
1995-04-18    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-04-25    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-05-02    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-05-09    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-05-16    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-05-23    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-05-30    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-06-06    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-06-13    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-06-20    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-06-27    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-07-03    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-07-11    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-07-18    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-07-25    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-08-01    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-08-08    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-08-15    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-08-22    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-08-29    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-09-05    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-09-12    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-09-19    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-09-26    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-10-03    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-10-10    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-10-17    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-10-24    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-10-31    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-11-07    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-11-14    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-11-21    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-11-28    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-12-05    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-12-12    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-12-19    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1995-12-26    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-01-02    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-01-09    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-01-16    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-01-23    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-01-30    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-02-06    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-02-13    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-02-20    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-02-27    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-03-05    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-03-12    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-03-19    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-03-26    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-04-02    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-04-09    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-04-16    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-04-23    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-04-30    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-05-07    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-05-14    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-05-21    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-05-28    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-06-04    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-06-11    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-06-18    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-06-25    COFFEE C - COFFEE, SUGAR & COCOA EXCHANGE   
1996-07-02    COFF

In [5]:
# For weather data, what I want is one row per observation, with each country's
# data represented in columns of that row

countries = ['BRA', 'COL', 'ETH', 'IDN', 'VNM']

# split weather into dfs for each country and rename columns appropriately
dfs = []
for country in countries:
    df = weather[weather['Country'] == country]
    df.rename(index=str, 
              columns={'Temperature (Monthly – C)':'{}_Temp'.format(country),
                       'Precip (mm)':'{}_Precip'.format(country)}, inplace=True)
    df.drop(columns=['Country'], inplace=True)
    dfs.append(df)

# combine separate countries' weather data into one frame indexed by date
weather = dfs[0]

for df in dfs[1:]:
    cols = df.columns.difference(weather.columns)
    weather = weather.merge(df[cols], left_index=True, right_index=True, how='outer')

In [7]:
# combine all data into one dataframe (using only the 1995-2015 window where they overlap)
dfs = [coffee['1995':'2016'], weather['1995':'2016'], fundamental['1995':'2016'], cot['1995':'2016']]

coffee_data = pd.concat(dfs, axis=1)

# Notes

A few things left to work on before I'm ready for basic EDA:

1. I need to deal with the mismatch of available data and narrow my study to the range of dates for which I have all of the data I need. Using decades of coffee prices for which I have no feature data is not helpful.

2. I need to comb through all of the columns that I have, particularly in the Commitment of Traders data. I expect the EDA/Feature Engineering stages will pare things down further, but I can probably eliminate a large number of columns quickly by sorting through the data dictionary. My guess is that many of the CoT features will be highly correlated with each other, so it probably makes more sense to start with a few of the most representative.

3. 'Missing' data - My data differ significantly in frequency, so I need to fill in gaps. As of now the plan to fill in missing values by the 'last observation carried forward' method, ensuring that for each point in time, I have the most recent (according to the data I have) entry for each column. I should think through the efficacy of this, versus trying to match up the frequency of my observarions better (i.e. do I need daily futures prices for my purposes?). How do I handle the fact that the same data point would represent 'new' information to the market on one day, but would be discounted at all later points in time?